<a href="https://colab.research.google.com/github/WilliamCollins-a/LLMHallucinations/blob/main/SemanticEntropy_UnitTESTS.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

MOUNT DRIVE

In [1]:
#Import the 'drive' module from Google Colab to enable access to Google Drive files and
from google.colab import drive
# Mount Google Drive to the Colab environment
drive.mount('/content/drive')


Mounted at /content/drive


LOAD THE MODEL AND DATASET

In [1]:
#Import library to read jupyter notebooks.
import nbformat

# Function to load a Jupyter notebook from the path.
def load_notebook(notebook_path):
    with open(notebook_path) as f:
        notebook = nbformat.read(f, as_version=4)
    return notebook

# Function to execute all code cells in a notebook
def execute_code_cells(notebook):
    from IPython import get_ipython
    ipython = get_ipython()
    for cell in notebook.cells:
        if cell.cell_type == 'code':
            ipython.run_cell(cell.source)

# Load and execute code from the notebook
notebook_path = '/content/drive/MyDrive/Colab Notebooks/model_loader.ipynb'
notebook = load_notebook(notebook_path)
execute_code_cells(notebook)

notebook_path = '/content/drive/MyDrive/Colab Notebooks/json_data_loader.ipynb'
notebook = load_notebook(notebook_path)
execute_code_cells(notebook)


Found existing installation: bitsandbytes 0.44.1
Uninstalling bitsandbytes-0.44.1:
  Successfully uninstalled bitsandbytes-0.44.1
Found existing installation: accelerate 1.0.1
Uninstalling accelerate-1.0.1:
  Successfully uninstalled accelerate-1.0.1
  Using cached bitsandbytes-0.44.1-py3-none-manylinux_2_24_x86_64.whl.metadata (3.5 kB)
  Using cached accelerate-1.0.1-py3-none-any.whl.metadata (19 kB)
Using cached bitsandbytes-0.44.1-py3-none-manylinux_2_24_x86_64.whl (122.4 MB)
Using cached accelerate-1.0.1-py3-none-any.whl (330 kB)
Loading the tokenizer...
Loading the model...


model.safetensors.index.json:   0%|          | 0.00/26.8k [00:00<?, ?B/s]

model-00001-of-00002.safetensors:   0%|          | 0.00/9.98G [00:00<?, ?B/s]

model-00002-of-00002.safetensors:   0%|          | 0.00/3.50G [00:00<?, ?B/s]

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

generation_config.json:   0%|          | 0.00/188 [00:00<?, ?B/s]

Streaming output truncated to the last 5000 lines.
{'knowledge': '"Faster" is the first single from Dutch symphonic metal/rock band Within Temptation\'s album "The Unforgiving". It had its worldwide radio première on 96.3 Rock Radio on 21 January 2011.The Unforgiving is the fifth studio album by Dutch symphonic metal band Within Temptation, released by Roadrunner Records on March 25, 2011. It was a concept album as one part of a transmedia storytelling project.The first single, "Faster", was released on January 21.', 'question': 'What radio station premiered Within Temptation\'s first single "Faster" from their fifth studio album on January 21,2011?', 'right_answer': '96.3 Rock Radio', 'hallucinated_answer': 'Within Temptation\'s first single "Faster" from their fifth studio album was premiered on a local radio station.'}
{'knowledge': 'Michel Dubois (born November 7, 1954) is a Canadian former professional ice hockey player who played in the World Hockey Association (WHA). Dubois play

FUNCTION THAT GENERATES RESPONSES

In [3]:
# Import Libraries
import os
import json
import random
import torch
from transformers import AutoModelForCausalLM, AutoTokenizer
import logging

# Configure logging to display information logs
logging.basicConfig(level=logging.INFO)

# Function to generate multiple responses for a given question
def generate_multiple_responses(question, model, tokenizer, num_responses=2, num_generations=3, temp_low=0.7, temp_high=1.2):
    responses = []  # List to store generated responses

    # Ensure pad_token is set
    if tokenizer.pad_token is None:
        tokenizer.pad_token = tokenizer.eos_token

    # Tokenize the input question and convert to tensor format
    input_ids = tokenizer(question, return_tensors="pt", padding=True).input_ids.to(model.device)

    # Generate multiple responses via loop
    for generation in range(num_generations):
        # Use temp_low for the first iteration, then temp_high for subsequent ones
        temp = temp_low if generation == 0 else temp_high

        for _ in range(num_responses):
            output = model.generate(
                input_ids,  # Input tensor for model
                max_length=150,  # Increased max length for more complete answers
                temperature=temp,  # Adjust temp for creativity of responses
                do_sample=True,  # Enable sampling for more diverse outputs
                pad_token_id=tokenizer.eos_token_id,  # Use eos token for padding
                max_new_tokens=50  # Limit to 50 new tokens for response
            )

            # Decode the generated text and strip out special tokens
            response = tokenizer.decode(output[0], skip_special_tokens=True).strip()

            # Check if the response starts with the question and remove it
            if response.startswith(question):
                response = response[len(question):].strip()

            # Avoid unhelpful or repetitive responses
            if response and len(response) > 5 and not any(phrase in response.lower() for phrase in ["thank you", "please provide"]):
                responses.append(response)
                logging.info('Generated response: %s', response)

    # Filter out duplicate or very similar responses
    filtered_responses = list(set(responses))
    return filtered_responses if filtered_responses else ["Sorry, I do not know the answer."]

# Load your JSON data
input_file = '/content/drive/MyDrive/Colab Notebooks/json_data_loader.ipynb'  # Adjust path accordingly
with open(input_file, 'r') as f:
    notebook_data = json.load(f)

# Extract and execute code cells to get questions
data = []
for cell in notebook_data['cells']:
    if cell['cell_type'] == 'code':
        exec(''.join(cell['source']))
        if 'data' in locals():
            data.extend(data)

# Sample and generate responses
num_samples = 1
num_responses_per_question = 2  # Set to 2 responses per question
num_generations = 3  # Number of generations to run
temp_high = 1.2  # Increased temperature for more creativity

if data:
    sampled_data = random.sample(data, min(num_samples, len(data)))  # Randomly sample a subset of questions

    responses = []  # List to store question-response pairs
    right_answers = []  # List to store right answers for sampled questions

    for item in sampled_data:
        question = item.get('question', '')  # Get the question from the data
        right_answer = item.get('right_answer', '')  # Get the right answer from the data

        if question:
            # Guiding prompt for LLM
            english_prompt = (f"Provide a concise, clear, and factual answer in English to the following question: {question}. "
                              "Do not repeat the question or prompt, add instructions, or include irrelevant details. "
                              "Answer directly and use simple and factual sentences."
                             )

            # Generate responses for the question
            responses_for_question = generate_multiple_responses(
                english_prompt, model, tokenizer, num_responses=num_responses_per_question, num_generations=num_generations, temp_low=0.7, temp_high=temp_high
            )

            # Append the question, right answer, and its generated responses to the list
            responses.append({
                'question': question,
                'responses': responses_for_question,
                'right_answer': right_answer  # Store the right answer
            })
            right_answers.append(right_answer)  # Collect right answers separately

    # Save generated responses to a JSON file
    output_file = '/content/drive/MyDrive/Colab Notebooks/generated_responses_test.json'  # Adjust path accordingly
    with open(output_file, 'w') as f:
        json.dump(responses, f, indent=4)

    print(f"Responses saved to {output_file}")
    print("Right Answers Collected:", right_answers)  # Display collected right answers
else:
    print("No data found in the notebook.")


Streaming output truncated to the last 5000 lines.
{'knowledge': 'Bulbophyllum is the largest genus in the orchid family Orchidaceae. With more than 2,000 species, it is also one of the largest genera of flowering plants, exceeded only by "Astragalus". The genus is named for the first chancellor of the German Empire Otto von Bismarck and the epithet for its only species, Bismarckia nobilis, comes from Latin for \'noble\'.', 'question': 'Which genus of flowering plant has more species Bulbophyllum or Bismarckia?', 'right_answer': 'Bulbophyllum', 'hallucinated_answer': 'Bismarckia has more species than Bulbophyllum.'}
{'knowledge': 'The 2005 Houston Texans season was the fourth season in franchise history. The team fired head coach Dom Capers after the season; he was replaced by Denver Broncos offensive coordinator Gary Kubiak.Ernest Dominic Capers (born August 7, 1950) is an American football coach and the current defensive coordinator for the Green Bay Packers of the National Football 

Both `max_new_tokens` (=50) and `max_length`(=150) seem to have been set. `max_new_tokens` will take precedence. Please refer to the documentation for more information. (https://huggingface.co/docs/transformers/main/en/main_classes/text_generation)



{'knowledge': ' After leading the perp walk of Bernie Madoff in 2008 and Raj Rajaratnam in 2009, Reuters described him as possibly "the most feared man on Wall Street."Raj Rajaratnam (Tamil: ராஜ் ராஜரத்தினம் ; born Rajakumaran Rajaratnam; June 15, 1957) is a Sri Lankan-American former hedge fund manager and billionaire founder of the Galleon Group, a New York-based hedge fund management firm.', 'question': 'Who is the former Sri Lankan- hedge fund manager that was investigated by BJ Kang for insider trading?', 'right_answer': 'Raj Rajaratnam', 'hallucinated_answer': 'BJ Kang investigated a hedge fund manager.'}
{'knowledge': 'Olakunle "Kay" Banjo (born December 3, 1992) is an American soccer player who plays for the Pittsburgh Riverhounds in the USL.The United Soccer League (USL), formerly known as USL Pro, is a professional men\'s soccer league in the United States and Canada that began its inaugural season in 2011.', 'question': 'Olakunle "Kay" Banjo (born December 3, 1992) is an Am

Both `max_new_tokens` (=50) and `max_length`(=150) seem to have been set. `max_new_tokens` will take precedence. Please refer to the documentation for more information. (https://huggingface.co/docs/transformers/main/en/main_classes/text_generation)
Both `max_new_tokens` (=50) and `max_length`(=150) seem to have been set. `max_new_tokens` will take precedence. Please refer to the documentation for more information. (https://huggingface.co/docs/transformers/main/en/main_classes/text_generation)
Both `max_new_tokens` (=50) and `max_length`(=150) seem to have been set. `max_new_tokens` will take precedence. Please refer to the documentation for more information. (https://huggingface.co/docs/transformers/main/en/main_classes/text_generation)
Both `max_new_tokens` (=50) and `max_length`(=150) seem to have been set. `max_new_tokens` will take precedence. Please refer to the documentation for more information. (https://huggingface.co/docs/transformers/main/en/main_classes/text_generation)
Both

Responses saved to /content/drive/MyDrive/Colab Notebooks/generated_responses_test.json
Right Answers Collected: ['33rd']


UNIT TEST - 1

In [5]:
# Import required libraries for testing
import unittest

# model and tokenizer are already loaded

class TestGenerateMultipleResponses(unittest.TestCase):

    """
    Unit tests for the generate_multiple_responses function.

    Tests include:
    1. test_generate_non_empty_responses: Checks that the function generates a non-empty list of responses for a valid question.
    2. test_unhelpful_responses_filtering: Verifies that the generated responses do not include unhelpful or irrelevant phrases such as 'thank you' or 'please provide'.
    """

    # Use the already loaded model and tokenizer
    def setUp(self):
        # Reference the preloaded model and tokenizer
        self.model = model  # The model you've already loaded
        self.tokenizer = tokenizer  # The tokenizer you've already loaded

    # Test if the function returns a non-empty list of responses
    def test_generate_non_empty_responses(self):
        question = "What is the capital of France?"
        responses = generate_multiple_responses(question, self.model, self.tokenizer, num_responses=2, num_generations=1)

        # Check if responses is a list and not empty
        self.assertIsInstance(responses, list, "The result should be a list.")
        self.assertTrue(len(responses) > 0, "The result list should not be empty.")

    # Test if function avoids unhelpful responses
    def test_unhelpful_responses_filtering(self):
        question = "What is 2 + 2?"
        responses = generate_multiple_responses(question, self.model, self.tokenizer, num_responses=2, num_generations=1)

        # Ensure none of the responses include unhelpful phrases
        unhelpful_phrases = ["thank you", "please provide"]
        for response in responses:
            self.assertFalse(
                any(phrase in response.lower() for phrase in unhelpful_phrases),
                f"Response contains unhelpful phrases: {response}"
            )

# Run the tests in the notebook
if __name__ == '__main__':
    unittest.main(argv=[''], verbosity=2, exit=False)


test_generate_non_empty_responses (__main__.TestGenerateMultipleResponses) ... Both `max_new_tokens` (=50) and `max_length`(=150) seem to have been set. `max_new_tokens` will take precedence. Please refer to the documentation for more information. (https://huggingface.co/docs/transformers/main/en/main_classes/text_generation)
Both `max_new_tokens` (=50) and `max_length`(=150) seem to have been set. `max_new_tokens` will take precedence. Please refer to the documentation for more information. (https://huggingface.co/docs/transformers/main/en/main_classes/text_generation)
ok
test_unhelpful_responses_filtering (__main__.TestGenerateMultipleResponses) ... Both `max_new_tokens` (=50) and `max_length`(=150) seem to have been set. `max_new_tokens` will take precedence. Please refer to the documentation for more information. (https://huggingface.co/docs/transformers/main/en/main_classes/text_generation)
Both `max_new_tokens` (=50) and `max_length`(=150) seem to have been set. `max_new_tokens` 

SEMANTIC ENTRPOY FUNCTION

In [2]:
import numpy as np
import logging
import torch
from transformers import AutoTokenizer, AutoModelForCausalLM
import json
import re

# Initialize the prediction cache
prediction_cache = {}

# Configure logging
logging.basicConfig(level=logging.DEBUG)  # or INFO based on your needs

def load_model_and_tokenizer(model_name="meta-llama/Llama-2-7b-chat-hf"):
    tokenizer = AutoTokenizer.from_pretrained(model_name)
    model = AutoModelForCausalLM.from_pretrained(model_name).to("cuda" if torch.cuda.is_available() else "cpu")
    return model, tokenizer


def equivalence_prompt_with_reasoning(text1, text2, question):
    prompt = f"""We are evaluating two answers to the question: "{question}"

    Possible Answer 1: {text1}
    Possible Answer 2: {text2}

    Please evaluate the factual relationship between these two answers.
    Explain your reasoning based on the information provided. After that, determine if the two answers:
    1. Have the same meaning or imply the same fact ("entailment"),
    2. Express opposite or contradictory facts ("contradiction"), or
    3. Do not relate to each other ("neutral").

    Provide reasoning starting with "Reasoning:" and end your response with "Label: [one of entailment, contradiction, neutral]".

    Your response should contain the reasoning followed by one of the labels: "entailment", "contradiction", or "neutral" in full.

    Response:"""
    return prompt

def parse_response(response):
    """Extract reasoning and label from the model's response using regex."""
    response = response.strip()  # Remove surrounding whitespace
    logging.debug("Raw response for parsing: %s", response)

    # Match reasoning which may span multiple lines
    reasoning_match = re.search(r'Reasoning:\s*((?:.|\n)*?)\s*Label:', response, re.IGNORECASE)

    # Match the label, ensuring we capture "entailment", "contradiction", or "neutral"
    label_match = re.search(r'Label:\s*(entailment|contradiction|neutral)', response, re.IGNORECASE)

    if reasoning_match and label_match:
        reasoning = reasoning_match.group(1).strip()  # Capture the reasoning text
        label = label_match.group(1).strip().lower()  # Normalize the label to lowercase
        return reasoning, label
    else:
        logging.warning("Failed to extract reasoning or label correctly from model output.")
        return "Reasoning not found", "neutral"


def predict(prompt, model, tokenizer):
    input_ids = tokenizer(prompt, return_tensors="pt").input_ids.to(model.device)
    output = model.generate(input_ids, max_length=1400, num_return_sequences=1, temperature=0.5)
    response = tokenizer.decode(output[0], skip_special_tokens=True)
    logging.debug("Raw Model Output: %s", response)
    print("Raw Model Output:", response)
    if not response.strip():
        logging.warning("Empty response received from model.")
    return response

def check_implication(text1, text2, model, tokenizer, example=None):
    if example is None:
        raise ValueError("Example must not be None.")

    prompt = equivalence_prompt_with_reasoning(text1, text2, example['question'])  # Fixed here
    logging.info('Input prompt: %s', prompt)

    cache_key = (text1, text2, example['question'])
    hashed = hash(cache_key)

    if hashed in prediction_cache:
        logging.info('Restoring cached prediction.')
        response = prediction_cache[hashed]
    else:
        response = predict(prompt, model, tokenizer)
        prediction_cache[hashed] = response

    logging.info('Raw Model Output: %s', response)

    reasoning, label = parse_response(response)

    return reasoning, label

def are_equivalent(text1, text2, model, tokenizer, example):
    # Check implication both ways
    reasoning1, label1 = check_implication(text1, text2, model, tokenizer, example)
    reasoning2, label2 = check_implication(text2, text1, model, tokenizer, example)

    logging.debug(f"Comparing: '{text1}' with '{text2}' - Labels: {label1}, {label2}")

    if label1 == 'entailment' and label2 == 'entailment':
        return True, reasoning1  # Both entail each other
    elif label1 == 'contradiction' and label2 == 'contradiction':
        return False, None  # Both contradict each other, should not be grouped
    elif label1 == 'neutral' and label2 == 'neutral':
        return False, None  # Both neutral, should not be grouped
    return False, None  # Any other case leads to not being equivalent

def get_semantic_ids(responses, model, tokenizer, example=None):
    semantic_set_ids = [-1] * len(responses)  # Initialize all IDs to -1
    next_id = 0  # ID counter
    labels = [None] * len(responses)  # Initialize labels list

    for i, response1 in enumerate(responses):
        if semantic_set_ids[i] == -1:  # If response1 has no ID yet
            semantic_set_ids[i] = next_id  # Assign current ID
            logging.info(f"Assigning new semantic ID {next_id} to response {i}: '{response1}'")
            print(f"Assigning ID {next_id} to response: {response1}")
            for j in range(i + 1, len(responses)):
                if semantic_set_ids[j] == -1:
                    equivalent, reasoning = are_equivalent(response1, responses[j], model, tokenizer, example)
                    if equivalent:
                        semantic_set_ids[j] = next_id  # Assign same ID to equivalent responses
                        logging.info(f"Assigning semantic ID {next_id} to equivalent response {j}: '{responses[j]}'")
                        print(f"Assigning ID {next_id} to equivalent response: {responses[j]}")
                        labels[j] = reasoning  # Store reasoning for equivalent responses
            next_id += 1  # Move to the next ID for the next unique group

    logging.info(f"Final assigned semantic_set_ids: {semantic_set_ids}")
    print(f"Assigned semantic_set_ids: {semantic_set_ids}")
    return semantic_set_ids, labels

def remap_semantic_ids(semantic_ids):
    """Ensure semantic IDs are continuous and remap them."""
    unique_ids = {id: idx for idx, id in enumerate(sorted(set(semantic_ids))) if id != -1}
    remapped_ids = [unique_ids.get(id, -1) for id in semantic_ids]
    logging.info(f"Remapped semantic_ids: {remapped_ids}")
    return remapped_ids

def cluster_assignment_entropy(semantic_ids):
    """Calculate the entropy of the cluster assignments."""
    n_generations = len(semantic_ids)
    counts = np.bincount(semantic_ids)
    probabilities = counts / n_generations
    return -np.sum(probabilities * np.log(probabilities + 1e-10))

def logsumexp_by_id(semantic_ids, log_likelihoods):
    """Compute logsumexp for each semantic group."""
    unique_ids = sorted(set(semantic_ids))
    log_likelihood_per_semantic_id = []

    for uid in unique_ids:
        id_indices = [pos for pos, x in enumerate(semantic_ids) if x == uid]
        id_log_likelihoods = [log_likelihoods[i] for i in id_indices]

        if id_log_likelihoods:  # Check if list is not empty
            logsumexp_value = np.log(np.sum(np.exp(id_log_likelihoods)))
            log_likelihood_per_semantic_id.append(logsumexp_value)

    return log_likelihood_per_semantic_id

def predictive_entropy(log_probs):
    """Calculate predictive entropy from log probabilities."""
    probabilities = np.exp(log_probs)
    entropy = -np.sum(probabilities * np.log(probabilities + 1e-10))
    return entropy

# Load model and tokenizer
model, tokenizer = load_model_and_tokenizer()

# Load generated responses from JSON
input_file = '/content/drive/MyDrive/Colab Notebooks/generated_responses_test.json'  # Adjust path accordingly
with open(input_file, 'r') as f:
    responses_data = json.load(f)

# Update the section where semantic IDs and labels are assigned
for item in responses_data:
    question = item['question']
    responses_for_question = item['responses']

    # Get semantic IDs and labels
    semantic_ids, labels = get_semantic_ids(responses_for_question, model, tokenizer, example={'question': question})

    # Remap semantic_ids to ensure they are continuous
    semantic_ids = remap_semantic_ids(semantic_ids)

    # Compute log likelihoods based on uniform distribution
    num_responses = len(responses_for_question)
    log_likelihoods = [torch.log(torch.tensor(1.0 / num_responses))] * num_responses

    # Calculate entropy
    cluster_entropy = cluster_assignment_entropy(semantic_ids)
    log_likelihood_per_semantic_id = logsumexp_by_id(semantic_ids, log_likelihoods)

    # Calculate predictive entropy
    predictive_entropies = [predictive_entropy(likelihood) for likelihood in log_likelihood_per_semantic_id]

    # Store results
    item['semantic_ids'] = semantic_ids
    item['cluster_entropy'] = cluster_entropy
    item['predictive_entropies'] = predictive_entropies

# Save updated responses data with semantic IDs and entropies to JSON
output_file = '/content/drive/MyDrive/Colab Notebooks/semantic_entropy_test.json'  # Adjust path accordingly
with open(output_file, 'w') as f:
    json.dump(responses_data, f, indent=4)


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

Assigning ID 0 to response: The freshman starting forward on the 2007–08 Duke Blue Devils was Kyrie Irving, who was selected with the first overall pick in the 2011 NBA Draft.
Raw Model Output: We are evaluating two answers to the question: "What number overall pick in the 2011 draft was the freshman starting forward on the 2007–08 Duke Blue Devils?"

    Possible Answer 1: The freshman starting forward on the 2007–08 Duke Blue Devils was Kyrie Irving, who was selected with the first overall pick in the 2011 NBA Draft.
    Possible Answer 2: Please do not use bullet points or numbered lists to provide the answer. Use full sentences. Provide the answer in a straightforward manner with no ambiguity or confusion. The question and answer are provided below: Question: What number overall pick in the

    Please evaluate the factual relationship between these two answers.
    Explain your reasoning based on the information provided. After that, determine if the two answers:
    1. Have the s

UNIT TEST-2

In [6]:

class TestEquivalencePrompt(unittest.TestCase):

    def test_equivalence_prompt_with_reasoning(self):
    """
    Test the `equivalence_prompt_with_reasoning` function.

    This test verifies that the prompt generated by the
    `equivalence_prompt_with_reasoning` function correctly
    incorporates the expected structural elements when given
    two statements and a question. The function is designed
    to assess the relationship between the two statements.

    The test checks for the following:

    1. The prompt should include the phrase "We are evaluating two answers",
       indicating that it clearly states the purpose of the evaluation.

    2. The prompt should contain the phrase "Reasoning:", ensuring that
       it prompts for an explanation of how the two statements relate
       to the question posed.

    3. The prompt should also include the phrase "Label:", which signifies
       that the output should classify the relationship between the answers,
       facilitating the evaluation process.

    """
    text1 = "Paris is the capital of France."
    text2 = "Paris is a city in France."
    question = "What is the capital of France?"

    # Call the function to generate the prompt
    prompt = equivalence_prompt_with_reasoning(text1, text2, question)

    # Check that the prompt contains the expected phrases
    self.assertIn("We are evaluating two answers", prompt)
    self.assertIn("Reasoning:", prompt)
    self.assertIn("Label:", prompt)

# Run test
unittest.TextTestRunner().run(unittest.TestLoader().loadTestsFromTestCase(TestEquivalencePrompt))


.
----------------------------------------------------------------------
Ran 1 test in 0.002s

OK


<unittest.runner.TextTestResult run=1 errors=0 failures=0>

UNIT TEST-3

In [9]:
class TestClusterEntropy(unittest.TestCase):
    def test_cluster_assignment_entropy(self):
        """
        Test the `cluster_assignment_entropy` function.

        This test checks if the computed entropy for different
        cluster assignments is non-negative. It also verifies that
        the entropy value reflects the diversity of cluster assignments,
        including specific cases for uniform distributions and empty lists.
        """
        # Test with a simple cluster assignment
        semantic_ids = [0, 0, 1, 1, 1]
        entropy = cluster_assignment_entropy(semantic_ids)
        self.assertGreaterEqual(entropy, 0)  # Entropy should be non-negative

        # Test with a uniform distribution
        semantic_ids_uniform = [0, 0, 1, 1]
        entropy_uniform = cluster_assignment_entropy(semantic_ids_uniform)
        self.assertGreater(entropy_uniform, 0)  # Expect positive entropy

        # Test with a single cluster
        semantic_ids_single = [0, 0, 0, 0]
        entropy_single = cluster_assignment_entropy(semantic_ids_single)
        self.assertAlmostEqual(entropy_single, 0, places=7)  # Check if close to 0

        # Test with an empty list
        semantic_ids_empty = []
        entropy_empty = cluster_assignment_entropy(semantic_ids_empty)
        self.assertAlmostEqual(entropy_empty, 0, places=7)  # Check if close to 0

# Running tests for Jupyter
def run_tests():
    unittest.TextTestRunner().run(unittest.TestLoader().loadTestsFromTestCase(TestClusterEntropy))

run_tests()


.
----------------------------------------------------------------------
Ran 1 test in 0.002s

OK
